Description:  This script produces Figure 2 (location of OKLMA sensors and KTLX radar)
which are the primary source of observational data used for analysis in this study

In [11]:
import numpy as np
import matplotlib.path as mpath
import shapely.affinity
import matplotlib.patches as mpatches
import pyproj
from shapely.geometry import MultiPolygon, Polygon, Point
from shapely.ops import transform as sh_transform
from functools import partial
import cartopy.io.shapereader as shpreader
import cartopy.feature as cfeature
import cartopy.crs as ccrs
import matplotlib.pyplot as plt
import pandas as pd
import os
import geopandas
import math

In [12]:
# This was a really helpful link to better understand the projections and transformations in cartopy
# https://stackoverflow.com/questions/42237802/plotting-projected-data-in-other-projectons-using-cartopy

wgs84_globe = pyproj.Proj(proj='latlong', ellps='WGS84')

# Shapely buffer in meters unit
# https://gis.stackexchange.com/questions/304914/python-shapely-intersection-with-buffer-in-meter

# The following function is a courtesy of https://stackoverflow.com/questions/44583674/intersect-two-shapely-polygons-on-the-earth-projection

def point_buff_on_globe(lat, lon, radius):
    """
    This function 
    """
    #First, you build the Azimuthal Equidistant Projection centered in the 
    # point given by WGS84 lat, lon coordinates
    aeqd = pyproj.Proj(proj='eqc', ellps='WGS84', datum='WGS84',
                       lat_0=lat, lon_0=lon)
    #You then transform the coordinates of that point in that projection
    project_coords = pyproj.transform(wgs84_globe, aeqd,  lon, lat)
    # Build a shapely point with that coordinates and buffer it in the aeqd projection
    aeqd_buffer = Point(project_coords).buffer(radius) 
    # Transform back to WGS84 each coordinate of the aeqd buffer.
    # Notice the clever use of sh_transform with partial functor, this is 
    # something that I learned here in SO. A plain iteration in the coordinates
    # will do the job too.
    projected_pol = sh_transform(partial(pyproj.transform, aeqd, wgs84_globe),
                          aeqd_buffer)
    return projected_pol

In [13]:
def draw_dual_dop(lon1,lat1,lon2,lat2,dist1,dist2,gdf,**kwargs):
    """
    Draws two concentric circles around the latlon coordinates provided
    
    Input:
    ______
    
    lon1,lat1 correspond to coordinate pairs for first point around which a circle is desired

    lon2,lat2 correspond to coordinate pairs for second point around which a circle is desired
    
    dist1: distance in kilometers from center (lon1,lat1) of circle 1 
    
    dist2: distance in kilometers from center (lon2,lat2) of circle 2
    
    gdf: geopandas geodataframe having info about scatter points to plot as station locations
    
    Note: order of keyword arguments should be lons, lats, and city names
    """

    # read US county shapefile to be overlaid on projected map
    reader = shpreader.Reader('./data_files/tl_2019_us_county/tl_2019_us_county.shp')

    counties = list(reader.geometries())
    
    # idea to plot counties from # idea from https://stackoverflow.com/questions/51106763/county-boarders-in-cartopy

    COUNTIES = cfeature.ShapelyFeature(counties, ccrs.PlateCarree()) 
    plt.figure(figsize=(12,12))
    ax = plt.axes(projection=ccrs.PlateCarree())

    # 
    pp1 = point_buff_on_globe(lat1,lon1,dist1*1000)
    pp2 = point_buff_on_globe(lat2,lon2,dist1*1000)
    combined_area1 = pp1.union(pp2)
    
    pp3 = point_buff_on_globe(lat1,lon1,dist2*1000)
    pp4 = point_buff_on_globe(lat2,lon2,dist2*1000)
    combined_area2 = (pp3.union(pp4)-combined_area1)

    ax.add_geometries([combined_area1],crs=ccrs.PlateCarree(),facecolor='mediumpurple',alpha=0.2,edgecolor='k',label="2D + 3D mapping")
    ax.add_geometries([combined_area2],crs=ccrs.PlateCarree(),facecolor='gold',alpha=0.4,edgecolor='k',label = "2D mapping only")
    
    gdf[gdf.status == 'NA'].plot(ax=ax, color='#ca0020',marker='s',label="Inactive")
    gdf[gdf.status == 'A'].plot(ax=ax, color='#4dac26',marker='s',label="Active")
    gdf[gdf.status == 'LOW'].plot(ax=ax, color='#e9a3c9',marker='s',label="Low detection")
    
    ax.add_feature(COUNTIES, facecolor='none', edgecolor='gray')
    ax.set_extent([-102, -95.5, 32.5, 37.5])
    
    ax.legend(loc='best')
       
    lons = kwargs.get('lons')
    print(lons)
    lats = kwargs.get('lats')
    cities = kwargs.get('cities')
    
    lons_final = []
    lats_final = []
    cities_final = []
    
    for key, value in lons.items(): 
        lons_final.append(value)
    print(lons_final)
    for key, value in lats.items():
        lats_final.append(value)
    for key, value in cities.items():
        cities_final.append(value)
        
    ax.scatter(lons_final,lats_final,transform=ccrs.PlateCarree(),marker='*',c='k')
    for i in range(len(cities_final)):
        ax.text(lons_final[i]+0.07, lats_final[i]+0.04,cities_final[i],transform=ccrs.PlateCarree(),fontsize=15)

    
    ax.scatter(lon_ktlx,lat_ktlx,transform=ccrs.PlateCarree(),marker='o',c='k')
    ax.text(lon_ktlx+0.07, lat_ktlx-0.02,'KTLX',transform=ccrs.PlateCarree(),fontsize=15)

    plt.show()

In [14]:
# load location data for all sensors belonging to OKLMA 
# The data is prepared and saved in the 'lma_df.txt' file

# load data in a pandas dataframe
df = pd.read_csv('./data_files/lma_df.txt',sep='\t')    

# we need only station name, latitude, and longitude information from the dataframe
df = df[df.columns[1:4]]
df.columns = ['stn_name','lat','lon']

df

stn_name        lat        lon
0    Chickasha SE  35.004345 -97.907304
1          Dutton  35.245175 -98.075489
2         El Reno  35.478505 -98.008938
3         Goldsby  35.132518 -97.518600
4             FAA  35.384373 -97.620829
5     Chickasha N  35.129969 -97.959265
6        Minco SE  35.279126 -97.917868
7      Middleberg  35.134734 -97.725763
8       Newcastle  35.256445 -97.658927
9         Minco W  35.362202 -98.039728
10          Yukon  35.440288 -97.778238
11  Altus Airport  34.696640 -99.340610
12   Prairie Hill  34.595020 -99.493680
13         Mangum  34.859230 -99.361210
14          Bluff  34.767940 -99.539240
15        Olustee  34.519520 -99.434940
16        Granite  34.973340 -99.448720
17         Zombie  34.711610 -99.080260

In [15]:
# Next, we want to calculate the centroids of central and western LMA array separately
# to be able to show their combined coverage area

# first we isolate central OK array
central_ok_df = df.iloc[:11]
central_ok_coords_df = central_ok_df[central_ok_df.columns[1:]]

# next is west OK array
west_ok_df = df.iloc[11:]
west_ok_coords_df = west_ok_df[west_ok_df.columns[1:]]

In [16]:

def centroid_geolocation(coords_df):
    """
    Retrieve the mean location from a group of latlon coordinate pairs
    
    Input:
    
    coords_df: Dataframe with two columns, one each for latitude and longitude for a set of points
    
    Returns:
    mean_location of the cluster of points specified in the dataframe
    """
    x = 0.0
    y = 0.0
    z = 0.0

    for i, coord in coords_df.iterrows():
        latitude = math.radians(coord.lat)
        longitude = math.radians(coord.lon)

        x += math.cos(latitude) * math.cos(longitude)
        y += math.cos(latitude) * math.sin(longitude)
        z += math.sin(latitude)

    total = len(coords_df)

    x = x / total
    y = y / total
    z = z / total

    central_longitude = math.atan2(y, x)
    central_square_root = math.sqrt(x * x + y * y)
    central_latitude = math.atan2(z, central_square_root)

    mean_location = {
        'latitude': math.degrees(central_latitude),
        'longitude': math.degrees(central_longitude)
        }
    
    return mean_location

In [17]:
# find the latitude and longitude of central OKLMA centroid
ctrl_lma_lat = centroid_geolocation(central_ok_coords_df)['latitude']
ctrl_lma_lon = centroid_geolocation(central_ok_coords_df)['longitude']

# find the latitude and longitude of western OKLMA centroid
west_lma_lat = centroid_geolocation(west_ok_coords_df)['latitude']
west_lma_lon = centroid_geolocation(west_ok_coords_df)['longitude']

In [18]:
# Next, we assign an active (A) or non-active (NA) status to each station location
# We get this info from the .dat.gz file (this one is for time 2140 UTC on May 19, 2013)

df['status'] = 'A'  # assign A to every station

# Next, we replace the column values in status column only 
# for those stations which were inactive during that period
def replace_vals(row):
    if (
        (row['stn_name'] == 'FAA') or         # These three stations were not working at all
        (row['stn_name'] == 'Olustee') or
        (row['stn_name'] == 'Zombie')
       ):
        row['status'] = 'NA'
    
    elif (
        (row['stn_name'] == 'Dutton') or      # These stations within central OKLMA had really low detection efficiency
        (row['stn_name'] == 'Chickasha N') or 
        (row['stn_name'] == 'Minco SE')
        ):
        row['status'] = 'LOW'
    return row

df = df.apply(replace_vals, axis=1)

In [19]:
# create a geopandas dataframe and use it to plot station locations
gdf = geopandas.GeoDataFrame(
    df, geometry=geopandas.points_from_xy(df.lon, df.lat)
)

In [20]:
cities = ['Tulsa','Edmond','Carney','Wichita Falls','Lubbock','Amarillo']
city_lons = [-95.9928,-97.4781,-97.0128,-98.4934,-101.8552,-101.8313]
city_lats = [36.1540,35.6528,35.8084,33.9137,33.5779,35.2220]

city_names_dict = { 'loc%d' % i: v for i, v in enumerate(cities)}
city_lons_dict = {'lon%d' % i: v for i,v in enumerate(city_lons)}
city_lats_dict = {'lat%d' % i: v for i,v in enumerate(city_lats)}

lon_koun = -97.46333; lat_koun = 35.23611
lon_ktlx = -97.2557; lat_ktlx = 35.3331

draw_dual_dop(ctrl_lma_lon,ctrl_lma_lat,west_lma_lon,west_lma_lat,100,150,gdf,lons=city_lons_dict,lats=city_lats_dict,cities=city_names_dict)

{'lon0': -95.9928, 'lon1': -97.4781, 'lon2': -97.0128, 'lon3': -98.4934, 'lon4': -101.8552, 'lon5': -101.8313}
[-95.9928, -97.4781, -97.0128, -98.4934, -101.8552, -101.8313]
